In [1]:
R.<x,y,A,B>=PolynomialRing(Rationals())

def reduce_poly_once(f):
    g = R(0)
    for t in f.monomials():
        if t.mod(y^2) == 0:
            g += f.monomial_coefficient(t)*R(t/y^2*(x^3+A*x+B))
        else:
            g += f.monomial_coefficient(t)*t
    return g

def reduce_poly(f):
    while f.degrees()[1] > 1: f = reduce_poly_once(f)
    return f

def reduce_point(P):
    return (reduce_poly(P[0]),reduce_poly(P[1]),reduce_poly(P[2]))

def dbl(P):
    x1= P[0]; y1=P[1]; z1=P[2]
    x3=x1^4-2*A*x1^2*z1^4-8*B*x1*z1^6+A^2*z1^8
    y3=x1^6+5*A*x1^4*z1^4+20*B*x1^3*z1^6-5*A^2*x1^2*z1^8-4*A*B*x1*z1^10-(A^3+8*B^2)*z1^12
    z3=2*y1*z1
    return reduce_point((x3,y3,z3))

def add(P,Q):
    if compare_point(P,Q): return dbl(P)
    x1=P[0]; y1=P[1]; z1=P[2]; x2=Q[0]; y2=Q[1]; z2=Q[2]
    x3 = A*(x1*z2^2+x2*z1^2)*z1^2*z2^2 + 2*B*z1^4*z2^4 + x1^2*x2*z2^2+x1*x2^2*z1^2-2*y1*y2*z1*z2
    y3 =(A*x2*z2+B*z2^3)*y2*z1^6 - (A*x1*z1+B*z1^3)*y1*z2^6+2*(x2^3*y1*z1^3 - x1^3*y2*z2^3) + 3*x1*x2*z1*z2*(x1*y2*z1 - x2*y1*z2)  + 3*y1*y2*(y1*z2^3 - y2*z1^3)
    z3 = x1*z2^2-x2*z1^2
    return reduce_point((x3,y3,z3))

def compare_point(P,Q):
    return (P[0]*Q[2]^2 == Q[0]*P[2]^2 and P[1]*Q[2]^3 == Q[1]*P[2]^3)

In [2]:
# compute the first 7 division polynomials using the group law
# NB: to avoid introducing extra factors compute P[2m+1] as P[m]+P[m+1] and P[2m]=P[m]+P[m]
# It will also work with arbitrary additions, but this may require removing common factors from the coordinates
# A more complicated version of reduce_point that does this is provided below.
P = [(R(0),R(1),R(0))]                   # point at infinity
P.append((R(x),R(y),R(1)))               # generic point P
P.append(dbl(P[1]))        # 2P = P + P
P.append(add(P[2],P[1]))   # 3P = 2P + P
P.append(dbl(P[2]))        # 4P = 2P + 2P
P.append(add(P[2],P[3]))   # 5P = 2P + 3P
P.append(dbl(P[3]))        # 6P = 3P + 3P
P.append(add(P[3],P[4]))   # 7P = 3P + 4P

In [4]:
for n in range(1,8): print("%d, %s, %s, %s"%(n,P[n][0], P[n][1], P[n][2]))

1, x, y, 1
2, x^4 - 2*x^2*A + A^2 - 8*x*B, x^6 + 5*x^4*A - 5*x^2*A^2 + 20*x^3*B - A^3 - 4*x*A*B - 8*B^2, 2*y
3, x^9 - 12*x^7*A + 30*x^5*A^2 - 96*x^6*B + 36*x^3*A^3 - 24*x^4*A*B + 9*x*A^4 + 48*x^2*A^2*B + 48*x^3*B^2 + 8*A^3*B + 96*x*A*B^2 + 64*B^3, -x^12*y - 22*x^10*y*A + 165*x^8*y*A^2 - 220*x^9*y*B + 92*x^6*y*A^3 + 528*x^7*y*A*B + 185*x^4*y*A^4 - 264*x^5*y*A^2*B + 1776*x^6*y*B^2 + 90*x^2*y*A^5 + 80*x^3*y*A^3*B + 960*x^4*y*A*B^2 + 3*y*A^6 + 132*x*y*A^4*B + 624*x^2*y*A^2*B^2 + 320*x^3*y*B^3 + 96*y*A^3*B^2 + 896*x*y*A*B^3 + 512*y*B^4, -3*x^4 - 6*x^2*A + A^2 - 12*x*B
4, x^16 - 40*x^14*A + 348*x^12*A^2 - 544*x^13*B + 1000*x^10*A^3 + 128*x^11*A*B + 1478*x^8*A^4 + 1760*x^9*A^2*B + 2944*x^10*B^2 + 1000*x^6*A^5 + 3584*x^7*A^3*B + 9696*x^8*A*B^2 + 348*x^4*A^6 + 1952*x^5*A^4*B + 14208*x^6*A^2*B^2 + 8704*x^7*B^3 - 40*x^2*A^7 + 1408*x^3*A^5*B + 2368*x^4*A^3*B^2 + 26624*x^5*A*B^3 + A^8 - 96*x*A^6*B + 1536*x^2*A^4*B^2 + 7680*x^3*A^2*B^3 + 15872*x^4*B^4 - 32*A^5*B^2 + 11264*x^2*A*B^4 - 256*A^2*B^4 + 4

In [5]:
# compute first 7 division polynomials using recurrence relations
M=8

psi=[R(0) for m in range(0,M+2)]
for m in range(0,5):
    psi[m]=P[m][2]
psi[3]=-psi[3]    # fix sign of psi_3 to match definition

# note that we need psi[m+2] to compute omega[m]
for n in range(5,M+2):
    m = n//2
    if n==2*m:
        psi[2*m]  =reduce_poly(R(psi[m]*(psi[m+2]*psi[m-1]^2-psi[m-2]*psi[m+1]^2)/(2*y)))
    else:
        psi[2*m+1]=reduce_poly(psi[m+2]*psi[m]^3-psi[m-1]*psi[m+1]^3)

phi=[R(0) for m in range(0,M)]
for m in range(1,M): phi[m] = reduce_poly(x*psi[m]^2-psi[m+1]*psi[m-1])

omega=[R(0) for m in range(0,M)]
omega[0]=1
omega[1]=y
for m in range(2,M): omega[m] = reduce_poly(R((psi[m+2]*psi[m-1]^2-psi[m-2]*psi[m+1]^2)/(4*y)))

In [8]:
# verify that we get the same result using the recurrences as when we used the group law
for m in range(1,M):
    print("%d: %s"%(m,compare_point(P[m],(phi[m],omega[m],psi[m]))))

1: True
2: True
3: True
4: True
5: True
6: True
7: True


In [9]:
P[7][2]

7*x^24 + 308*x^22*A - 2954*x^20*A^2 + 3944*x^21*B - 19852*x^18*A^3 - 112*x^19*A*B - 35231*x^16*A^4 - 92568*x^17*A^2*B - 42896*x^18*B^2 - 82264*x^14*A^5 - 31808*x^15*A^3*B - 571872*x^16*A*B^2 - 111916*x^12*A^6 - 161840*x^13*A^4*B - 615360*x^14*A^2*B^2 - 829696*x^15*B^3 - 42168*x^10*A^7 - 608160*x^11*A^5*B - 297472*x^12*A^3*B^2 - 2132480*x^13*A*B^3 + 15673*x^8*A^8 - 425712*x^9*A^6*B - 1192800*x^10*A^4*B^2 - 2603776*x^11*A^2*B^3 - 928256*x^12*B^4 + 14756*x^6*A^9 - 53824*x^7*A^7*B - 831936*x^8*A^5*B^2 - 3727360*x^9*A^3*B^3 - 3293696*x^10*A*B^4 + 1302*x^4*A^10 + 57288*x^5*A^8*B - 190400*x^6*A^6*B^2 - 1314560*x^7*A^4*B^3 - 7069440*x^8*A^2*B^4 - 1555456*x^9*B^5 + 196*x^2*A^11 + 1680*x^3*A^9*B + 134400*x^4*A^7*B^2 - 168448*x^5*A^5*B^3 - 2293760*x^6*A^3*B^4 - 7127040*x^7*A*B^5 - A^12 + 392*x*A^10*B + 3696*x^2*A^8*B^2 + 152320*x^3*A^6*B^3 + 394240*x^4*A^4*B^4 - 3698688*x^5*A^2*B^5 - 2809856*x^6*B^6 + 160*A^9*B^2 + 7168*x*A^7*B^3 + 96768*x^2*A^5*B^4 + 831488*x^3*A^3*B^5 - 3039232*x^4*A*B^6 + 3328

In [10]:
# this is a more thorough point reduction function that removes common factors
def reduce_point(P):
    x3 = reduce_poly(P[0])
    y3 = reduce_poly(P[1])
    z3 = reduce_poly(P[2])
    z32 = reduce_poly(z3^2)
    z33 = reduce_poly(z3^3)
    h = R((y3*numerator(x3/z32)) / (x3*numerator(y3/z33)))
    x3 = R(x3/h^2); y3 = R(y3/h^3); z3 = R(z3/h)
    if z3.mod(y) == 0 and x3.mod(x^3+A*x+B) == 0 and y3.mod((x^3+A*x+B)^2) == 0:
        z3 = R(z3/y); x3 = R(x3/(x^3+A*x+B)); y3 = R(y*y3/(x^3+A*x+B)^2)
    if z3.mod(x^3+A*x+B) == 0 and x3.mod(x^3+A*x+B) == 0 and y3.mod((x^3+A*x+B)*y) == 0:
        z3 = R(y*z3/(x^3+A*x+B)); x3 = R(x3/(x^3+A*x+B)); y3 = R(y3/(y*(x^3+A*x+B)))
    xc = gcd([int(c) for c in x3.coefficients()])
    yc = gcd([int(c) for c in y3.coefficients()])
    zc = gcd([int(c) for c in z3.coefficients()])
    if zc%2 == 0 and xc%4 == 0 and yc%8 == 0:
        z3 = R(z3/2); x3 = R(x3/4); y3 = R(y3/8);
    xc = gcd([int(c) for c in x3.coefficients()])
    yc = gcd([int(c) for c in y3.coefficients()])
    zc = gcd([int(c) for c in z3.coefficients()])
    if zc%2 == 0 and xc%4 == 0 and yc%8 == 0:
        z3 = R(z3/2); x3 = R(x3/4); y3 = R(y3/8);
    return (x3,y3,z3)

In [12]:
print(P[7][1])

x^72*y + 612*x^70*y*A - 162978*x^68*y*A^2 + 35304*x^69*y*B + 292468*x^66*y*A^3 - 3434544*x^67*y*A*B - 136715887*x^64*y*A^4 + 89908104*x^65*y*A^2*B - 50917584*x^66*y*B^2 - 2878540896*x^62*y*A^5 - 200586496*x^63*y*A^3*B - 189519264*x^64*y*A*B^2 - 27433746480*x^60*y*A^6 - 26018484672*x^61*y*A^4*B - 16463183616*x^62*y*A^2*B^2 + 1762855424*x^63*y*B^3 - 199034507872*x^58*y*A^7 - 246004159104*x^59*y*A^5*B - 406415978496*x^60*y*A^3*B^2 - 85929177600*x^61*y*A*B^3 - 609871362252*x^56*y*A^8 - 3109591425472*x^57*y*A^6*B - 2039624365440*x^58*y*A^4*B^2 - 3320266882560*x^59*y*A^2*B^3 - 324496236288*x^60*y*B^4 - 2174973922000*x^54*y*A^9 - 7471676126976*x^55*y*A^7*B - 33552575179008*x^56*y*A^5*B^2 - 12713923320320*x^57*y*A^3*B^3 - 17693603873280*x^58*y*A*B^4 - 14130630520248*x^52*y*A^10 + 4101348572640*x^53*y*A^8*B - 130922115667200*x^54*y*A^6*B^2 - 169642743723520*x^55*y*A^4*B^3 - 125014623694080*x^56*y*A^2*B^4 - 30593851180032*x^57*y*B^5 - 68900083189392*x^50*y*A^11 - 8605433289024*x^51*y*A^9*B - 217